<a href="https://colab.research.google.com/github/BDonadelli/Codigos-em-financas/blob/main/momentum_simples.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
ticker="TASA4"
import yfinance as yf
data = yf.download(ticker+'.SA',
                    # start="2017-01-01",end="2017-04-30", 
                    period='max',
                    auto_adjust=True)
data

[*********************100%%**********************]  1 of 1 completed


Open       High        Low      Close  Volume
Date                                                          
2000-01-03   2.582747   2.582747   2.582747   2.582747       0
2000-01-04   2.582747   2.582747   2.582747   2.582747       0
2000-01-05   2.582747   2.582747   2.582747   2.582747       0
2000-01-06   2.582747   2.582747   2.582747   2.582747       0
2000-01-07   2.582747   2.582747   2.582747   2.582747       0
...               ...        ...        ...        ...     ...
2024-09-04  11.170000  11.270000  11.100000  11.110000  183300
2024-09-05  11.110000  11.200000  11.040000  11.200000  365000
2024-09-06  11.200000  11.310000  11.060000  11.250000  322300
2024-09-09  11.250000  11.280000  11.130000  11.150000  196900
2024-09-10  11.150000  11.240000  11.110000  11.220000  138100

[6202 rows x 5 columns]

In [2]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

In [3]:

def strategy(returns, window=1, short=True):
    '''
        estratégia:
            - compra se o retorno na janela é >0
            - venda  se o retorno na janela é <0, opcionalmente 
    '''

    if short:
        position = returns.rolling(window).mean().map(lambda x: -1 if x <= 0 else 1)
    else:
        position = returns.rolling(window).mean().map(lambda x: 0 if x <= 0 else 1)
    performance = position.shift(1) * returns
    return performance


In [4]:
## log returns
returns = np.log(data['Close'])-np.log(data['Close'].shift(1))
returns = returns.dropna()

performance = strategy(returns,5 , False).dropna()
performance.tail()


Date
2024-09-04   -0.005386
2024-09-05    0.000000
2024-09-06    0.004454
2024-09-09   -0.000000
2024-09-10    0.006258
Name: Close, dtype: float64

In [5]:
n_years = (performance.index.max() - performance.index.min()).days / 252
perf_cum = np.exp(performance.cumsum())
tot = perf_cum.iloc[-1] - 1
ann = perf_cum.iloc[-1] ** (1 / n_years) - 1
vol = performance.std() * np.sqrt(252)
rfr = 0.1075
sharpe = (ann - rfr) / vol
print("Retorno da estratégia")
print(f"\t{tot*100:.2f}% retorno total" +
      f"\n\t{ann*100:.2f}% anual" +
      f"\n\t{sharpe:.2f} Sharpe Ratio")


Retorno da estratégia
	618.27% retorno total
	5.67% anual
	-0.13 Sharpe Ratio


In [6]:
ret = np.exp(returns.cumsum())
b_tot = ret.iloc[-1] - 1
b_ann = ret.iloc[-1] ** (1 / n_years) - 1
b_vol = returns.std() * np.sqrt(252)
b_sharpe = (b_ann - rfr) / b_vol
print(f"Buy-and-Hold:" +
      f"\n\t{b_tot*100:.2f}%  retorno total" +
      f"\n\t{b_ann*100:.2f}% anual" +
      f"\n\t{b_sharpe:.2f} Sharpe Ratio")

Buy-and-Hold:
	334.42%  retorno total
	4.19% anual
	-0.11 Sharpe Ratio


In [7]:
# simula estratégia em janelas de  3, 5, ...  dias
periods = [3, 5, 7, 11, 13, 17, 23, 29, 31, 37, 43 , 47, 53, 59,61, 67,71,87]
# periods = [43,59]

In [8]:
perf_dict = {'tot_ret': {'buy_and_hold': (np.exp(returns.sum()) - 1)}}
perf_dict['ann_ret'] = {'buy_and_hold': b_ann}
perf_dict['sharpe'] = {'buy_and_hold': b_sharpe}
for p in periods:
    log_perf = strategy(returns, window=p )
    perf = np.exp(log_perf.cumsum())
    perf_dict['tot_ret'][p] = (perf.iloc[-1] - 1)
    ann = (perf.iloc[-1] ** (1/n_years) - 1)
    perf_dict['ann_ret'][p] = ann
    vol = log_perf.std() * np.sqrt(252)
    perf_dict['sharpe'][p] = (ann - rfr) / vol

In [13]:
import plotly.graph_objects as go
import numpy as np

fig = go.Figure()

fig.add_trace(go.Scatter(
    x=returns.index, 
    y=(np.exp(returns.cumsum()) - 1) * 100, 
    mode='lines', 
    name=ticker
))

for p in periods:
    log_perf = strategy(returns, window=p)
    perf = np.exp(log_perf.cumsum())
    fig.add_trace(go.Scatter(
        x=returns.index, 
        y=(perf - 1) * 100, 
        mode='lines', 
        name=f'{p}-Day Mean'
    ))

fig.update_layout(
    title='Retorno Acumulado',
    xaxis_title='Data',
    yaxis_title='Retorno (%)',
    legend_title='Estratégias',
    showlegend=True
)

fig.show()


In [10]:
fig_ann_ret = go.Figure()

# Adicionando as barras de Retorno Anualizado
fig_ann_ret.add_trace(go.Bar(
    x=[f'{k}-Day Mean' if isinstance(k, int) else ticker for k in perf_dict['ann_ret'].keys()],
    y=[v * 100 for v in perf_dict['ann_ret'].values()],
    name='Retorno Anualizado'
))

# Ajustando o layout do gráfico
fig_ann_ret.update_layout(
    title='Retorno Anualizado por Estratégia',
    xaxis_title='Estratégia',
    yaxis_title='Retorno (%)',
    xaxis_tickangle=45,
    showlegend=False
)

# Exibindo o gráfico
fig_ann_ret.show()


In [11]:
fig_sharpe = go.Figure()

# Adicionando as barras de Sharpe Ratio
fig_sharpe.add_trace(go.Bar(
    x=[f'{k}-Day Mean' if isinstance(k, int) else ticker for k in perf_dict['sharpe'].keys()],
    y=[v for v in perf_dict['sharpe'].values()],
    name='Sharpe Ratio'
))

# Ajustando o layout do gráfico
fig_sharpe.update_layout(
    title='Sharpe Ratio por Estratégia',
    xaxis_title='Estratégia',
    yaxis_title='Sharpe Ratio',
    xaxis_tickangle=45,
    showlegend=False
)

# Exibindo o gráfico
fig_sharpe.show()
